* build overall dictionary for clf and reg

In [ ]:
import os, sys
# os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"
# The GPU id to use, usually either "0" or "1"
# os.environ["CUDA_VISIBLE_DEVICES"]="1" 
import keras
import sent2vec
import seq2seq
from seq2seq.models import AttentionSeq2Seq
from seq2seq.models import Seq2Seq
from keras.utils import multi_gpu_model
import tensorflow as tf
import numpy as np
import pandas as pd
import os
import shutil
import pickle
import tqdm
from tqdm import tqdm
import math

import numpy as np
from random import shuffle
from math import log, floor
import pandas as pd
import tensorflow as tf
import tensorboard as tb
from keras import backend as K
from keras.models import *
from keras.layers import *
from keras.activations import *
from keras.callbacks import *
from keras.utils import *
from keras.layers.advanced_activations import *
from keras import *
from keras.engine.topology import *
from keras.optimizers import *
import gensim
from gensim.models.word2vec import *
from keras.preprocessing.text import *
from keras.preprocessing.sequence import *
from keras.utils import *
from sklearn.model_selection import *
import random
from random import shuffle
import re
from operator import itemgetter
from keras.utils.generic_utils import *
from keras import regularizers
import string
import unicodedata as udata
import pickle
from keras.applications import *
from keras.preprocessing.image import *
import pause, datetime
import matplotlib.pyplot as plt
from sklearn.naive_bayes import *
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import wordpunct_tokenize
from nltk import word_tokenize
from nltk.stem.porter import *
from nltk.tokenize import RegexpTokenizer
from collections import Counter
import functools

In [16]:
ori_df = pd.read_csv('data/combine_data.csv')
ori_df

text        label
0      house dem aide we didn t even see comey s lett...            1
1      ever get the feeling your life circles the rou...            0
2      why the truth might get you fired october the ...            1
3      videos civilians killed in single us airstrike...            1
4      print an iranian woman has been sentenced to s...            1
5      in these trying times jackie mason is the voic...            0
6      ever wonder how britain s most iconic pop pian...            1
7      paris france chose an idealistic traditional c...            0
8      donald j trump is scheduled to make a highly a...            0
9      a week before michael t flynn resigned as nati...            0
10     organizing for action the activist group that ...            0
11     the bbc produced spoof on the real housewives ...            0
12     the mystery surrounding the third reich and na...            1
13     clinton campaign demands fbi affirm trump s ru...            1
14     yes there are paid government trolls on social...            1
15     guillermo barros schelotto was not the first a...            0
16     the scandal engulfing wells fargo toppled its ...            0
17     a caddo nation tribal leader has just been fre...            1
18     fbi closes in on hillary posted on home headli...            1
19     wednesday after donald trump s press conferenc...            0
20     email since donald trump entered the election ...            1
21     screenwriter ryan murphy who has produced the ...            0
22     sunday on msnbc s am joy actor and director ro...            0
23     massachusetts cop s wife busted for pinning fa...            1
24     orders for abortion pills by women in seven la...            0
25     email in an historic move the united nations f...            1
26     jerusalem islamic state sympathizers and milit...            0
27     humiliated hillary tries to hide what camera c...            1
28     andrea tantaros a former fox news host charged...            0
29     hillary clinton sat in the hideaway study off ...            0
...                                                  ...          ...
46560  says ron saunders made the choice to stand wit...        false
46561  since president obama took office there are ov...    half-true
46562  people in the top tax bracket these so called ...  barely-true
46563  barack obama has pledged to reduce the size of...        false
46564  large majorities of the public oppose major ch...         true
46565                       fidel castro endorses obama    pants-fire
46566  says spending in the fiscal budget was lower t...         true
46567  there is no statistical evidence that bail bon...        false
46568  household incomes are down more than since the...  mostly-true
46569  the u s is spending one out of every six defen...         true
46570  says personhood legislation she sponsored woul...    half-true
46571  the republican party fought very hard in the s...         true
46572  a major part of the climate change bill sponso...        false
46573  ohios credit rating is as high as you can get aa         false
46574  says every day of a special session costs taxp...        false
46575   we ve excluded lobbyists from policymaking jobs         false
46576  the federal deficit would pay for gallons of n...    half-true
46577  says george flinn has been a no show at schedu...        false
46578  social security and other federal checks may n...    half-true
46579  tsa started off with screeners and the agency ...    half-true
46580  the proposed excise tax on cadillac health pla...  mostly-true
46581  i supported the surge i argued for it i m the ...        false
46582  says u s rep charles bass wants to privatize s...  barely-true
46583  more americans believe the moon landing was fa...    half-true
46584  in the past two years democrats have spent mor...   pants-fire
46585  for the first time in more than a decade impor...    ha

In [18]:
ori_li = ori_df.text.tolist()
ori_li
kk = " ".join(ori_li)
kk = set(kk.split(' '))
len(kk)

158141

In [2]:
with open('data/stop_words.txt') as f:
    stop_words_list = f.read().splitlines() #stop_list1
stop_list2 = pickle.load(open('data/stop_list2.pkl','rb'))
ps = PorterStemmer() # Stemming
stop_words = set(stopwords.words('english')) #Stopword
short = ['.', ',', '"', "\'", '?', '!', ':', ';', '(', ')', '[', ']', '{', '}', "'at",
         "_","`","\'\'","--","``",".,","//",":","___",'_the','-',"'em",".com",
                   '\'s','\'m','\'re','\'ll','\'d','n\'t','shan\'t',"...","\'ve",'u']
stop_words_list.extend(short)
stop_words_list.extend(stop_list2)
stop_words.update(stop_words_list)

In [3]:
def preprocess(texts):
    tokens = [i for i in word_tokenize(texts.lower()) if i not in stop_words]  # Tokenization.# Lowercasing
    token_result = ''
    token_result_ = ''
    for i,token in enumerate(tokens): #list2str
        token_result += ps.stem(token) + ' '
    token_result = ''.join([i for i in token_result if not i.isdigit()])
    token_result = [i for i in word_tokenize(token_result) if i not in stop_words]
    for i,token in enumerate(token_result):
        token_result_ += token + ' '
    return token_result_

In [10]:
test_df = pd.read_csv('data/test.csv').astype('str')
test_df_t = test_df['text'].apply(preprocess)
test_df_t
# pd.DataFrame(columns=)

0       palo alto calif. — year scorn polit process si...
1       russian warship readi strike terrorist near al...
2       video # nodapl nativ american leader vow stay ...
3       ’ succeed tri differ sport tim tebow heisman q...
4       min ago view comment like 'for time histori ’ ...
5       trump usa antiqu hero clinton presid .. | sour...
6       sunday nbc ’ “ meet press ” hous minor leader ...
7       home / *articl bound* / weekli featur profil –...
8       urban popul boom make climat chang wors post o...
9                                                receipt 
10      seen pro-hillari tv ad disgrac gen. john allen...
11      sourc cnbc articl robert ferri arctic sea ice ...
12      written shaun bradley mandatori vaccin open ne...
13      store communist terror small busi owner blue c...
14      conserv tribun programm clinton “ clint ” curt...
15      berlin — palm flip plunk vend machin appar pin...
16      foxborough mass — n. f. l. like portray big fa...
17      berkel

In [11]:
test_df

id                                              title  \
0     20800  Specter of Trump Loosens Tongues, if Not Purse...   
1     20801  Russian warships ready to strike terrorists ne...   
2     20802  #NoDAPL: Native American Leaders Vow to Stay A...   
3     20803  Tim Tebow Will Attempt Another Comeback, This ...   
4     20804                    Keiser Report: Meme Wars (E995)   
5     20805  Trump is USA's antique hero. Clinton will be n...   
6     20806  Pelosi Calls for FBI Investigation to Find Out...   
7     20807            Weekly Featured Profile – Randy Shannon   
8     20808  Urban Population Booms Will Make Climate Chang...   
9     20809                                                nan   
10    20810  184 U.S. generals and admirals endorse Trump f...   
11    20811               “Working Class Hero” by John Brennon   
12    20812  The Rise of Mandatory Vaccinations Means the E...   
13    20813                Communists Terrorize Small Business   
14    20814  Computer Programmer Comes Forward, Admits To B...   
15    20815  Thieves Take a Chunk of Change, All 221 Pounds...   
16    20816  New England Patriots’ Owner, Still Sore at N.F...   
17    20817  College Republicans, YAF Sue Berkeley over Ann...   
18    20818  Trump Melts Down And Accuses The US Postal Ser...   
19    20819  Visiting Madagascar? Leave Red Swimsuits (and ...   
20    20820  Reese’s Peanut Butter Cups – Cheap and Full of...   
21    20821  President Obama and President-Elect Donald Tru...   
22    20822                                                nan   
23    20823  The Real Numbers in Florida: Trump Winning by ...   
24    20824  Ann Coulter On C-Span Quotes VDARE.com’s Brime...   
25    20825  ‘Age of Empires’: How 2 Dynasties of Art Forge...   
26    20826  Because STUPID! NARAL created deck of ‘Gender ...   
27    20827  Bill Weld, Running as a Libertarian, Likens Do...   
28    20828  How Housing’s New Players Spiraled Into Banks’...   
29    20829                              Переплюнуть Калигулу…   
...     ...                                                ...   
5170  25970  Reinventing Democracy in America Starts by Vot...   
5171  25971  Report: Palestinian Delegation to Meet Trump O...   
5172  25972  The Postmodern Stalinism of the Western Media ...   
5173  25973  WATCH: Iraqi Christians on U.S. President - ‘W...   
5174  25974                                     Links 11/11/16   
5175  25975  Trump Weighs In as Senate Slides Toward Showdo...   
5176  25976  Limbaugh on Comey Hearing: Message to Trump Is...   
5177  25977  Toure: Black-on-Black Crime in Chicago Not a P...   
5178  25978  The Grim Logic Behind Syria’s Chemical Weapons...   
5179  25979  Trepidation at City College in Wake of Preside...   
5180  25980  Singers in Russian Military Choir Among 92 Fea...   
5181  25981  U.S. Near Bottom in Public ‘Confidence in Elec...   
5182  25982  After 6,000 Exorcisms, Priest Says ‘The Devil ...   
5183  25983  WSJ: White House Opens Door to Democrats in Wa...   
5184  25984  Fox Sports’ Clay Travis Rips ’Hypocritical’ Ni...   
5185  25985  Pillars of the West Shaken by ‘Brexit,’ but Th...   
5186  25986                  The Fed Plans for the Next Crisis   
5187  25987  ‘The Market Is Saturated’: Brooklyn’s Rental B...   
5188  25988  The Dangers of ‘Polypharmacy,’ the Ever-Mounti...   
5189  25989  Amazon extends olive branch to Megyn Kelly ove...   
5190  25990  Secret Service Shoots Man Near White House - T...   
5191  25991  E3 Hands-On with ’South Park: The Fractured bu...   
5192  25992  Earth To Ammosexuals: NRA Admits No One Is Com...   
5193  25993  Toyota Recalls 1.4 Million Vehicles as 2nd Maj...   
5194  25994  Trump on If ’Tapes’ Exist of Comey Conversatio...   
5195  25995  The Bangladeshi Traffic Jam That Never Ends - ...   
5196  25996  John Kasich Signs One Abortion Bill in Ohio bu...   
5197  25997  California Today: What, Exactly, Is in Your Su...   
5198  25998  300 US Marines To Be Deployed To Rus

In [13]:
test_df = pd.concat([test_df['id'].astype(int),test_df_t],axis=1)
test_df['label']=1
test_df

id                                               text  label
0     20800  palo alto calif. — year scorn polit process si...      1
1     20801  russian warship readi strike terrorist near al...      1
2     20802  video # nodapl nativ american leader vow stay ...      1
3     20803  ’ succeed tri differ sport tim tebow heisman q...      1
4     20804  min ago view comment like 'for time histori ’ ...      1
5     20805  trump usa antiqu hero clinton presid .. | sour...      1
6     20806  sunday nbc ’ “ meet press ” hous minor leader ...      1
7     20807  home / *articl bound* / weekli featur profil –...      1
8     20808  urban popul boom make climat chang wors post o...      1
9     20809                                           receipt       1
10    20810  seen pro-hillari tv ad disgrac gen. john allen...      1
11    20811  sourc cnbc articl robert ferri arctic sea ice ...      1
12    20812  written shaun bradley mandatori vaccin open ne...      1
13    20813  store communist terror small busi owner blue c...      1
14    20814  conserv tribun programm clinton “ clint ” curt...      1
15    20815  berlin — palm flip plunk vend machin appar pin...      1
16    20816  foxborough mass — n. f. l. like portray big fa...      1
17    20817  berkeley colleg republican young america ’ fou...      1
18    20818  trump warn support postal servic tri steal ele...      1
19    20819  visit certain beach northeastern madagascar ’ ...      1
20    20820  anya v man h.b rees creat peanut butter cup mr...      1
21    20821  presid obama president-elect donald trump meet...      1
22    20822  vers state nation insecur director nation inse...      1
23    20823  octob dailystorm win hard th wo matter buss wo...      1
24    20824                                                         1
25    20825  epic better metropolitan museum art brought pe...      1
26    20826  stupid naral creat deck ‘ gender card ’ hillar...      1
27    20827  william f. weld republican governor massachuse...      1
28    20828  hous crisi sent american economi brink disast ...      1
29    20829  происшествия с лёгкой руки итальянского режисс...      1
...     ...                                                ...    ...
5170  25970  reinvent democraci america start vote build ac...      1
5171  25971  jerusalem post report deleg palestinian offici...      1
5172  25972  origin appear chronicl magazin latest sputnik ...      1
5173  25973  new video number christian live iraq express a...      1
5174  25974  ten-step program adjust president-elect trump ...      1
5175  25975  presid donald trump devot friday ’ weekli whit...      1
5176  25976  monday nation syndic radio conserv talker rush...      1
5177  25977  saturday “ joy ” broadcast msnbc msnbc contrib...      1
5178  25978  beirut lebanon — diplomat situat look bright p...      1
5179  25979  student citi colleg new york flagship largest ...      1
5180  25980  sochi russia — russian aircraft bound syria ca...      1
5181  25981  voter think clinton broke law … twice think tr...      1
5182  25982  mexican priest perform exorc career say fear d...      1
5183  25983  republican unabl reach deal repeal replac obam...      1
5184  25984  monday version fox sport radio “ outkick cover...      1
5185  25985  london — day blend dull ritual undeni histor i...      1
5186  25986  recent address jackson hole monetari polici co...      1
5187  25987  roof build near atlant termin transit hub broo...      1
5188  25988  dr. caleb alexand know easili older peopl fall...      1
5189  25989  .. @ pm est establish tie intellihub — look fo...      1
5190  25990  washington — man approach white hous friday br...      1
5191  25991  titl south park fractur essenti set comed tone...      1
5192  25992  earth ammosexu nra admit come gun video natali...      1
5193  25993  public concern faulti automobil airbag spread ...      1
5194  25994  pre trump “ tape ” exist convers comey ” ’ tel...      1
5195  25995  dysfun

In [ ]:
test_df.to_csv('data/testing.csv',index=False)

In [9]:
token_df = ori_df['text'].apply(preprocess)
token_df

0        hous dem aid comey letter jason chaffetz tweet...
1        feel life circl roundabout head straight line ...
2        truth octob tension intellig analyst polit pol...
3        video civilian kill singl airstrik identifi ra...
4        print iranian woman sentenc year prison iran r...
5        tri time jacki mason voic reason week exclus c...
6        wonder britain icon pop pianist long flight pi...
7        pari franc chose idealist tradit candid sunday...
8        donald j trump schedul make highli anticip vis...
9        week michael flynn resign nation secur advis s...
10       organ action activist group morph barack obama...
11       bbc produc spoof real housew tv programm comed...
12       mysteri surround reich nazi germani subject de...
13       clinton campaign demand fbi affirm trump russi...
14       ye paid govern troll social media blog forum w...
15       guillermo barro schelotto argentin player set ...
16       scandal engulf fargo toppl chairman chief exec.

In [14]:
token_li = token_df.tolist()
new_string = "".join(token_li)
token_set = set(new_string.split(' '))
token_list = list(token_set)
for token in token_list: #13551=>13406
    if len(token)<3:
        token_list.remove(token)
token_list = sorted(token_list)
print(len(token_list))
token_list

117748


['aaa',
 'aaaaah',
 'aaaaggg',
 'aaaahhh',
 'aaah',
 'aaahhh',
 'aaajiao',
 'aaani',
 'aaargh',
 'aab',
 'aabb',
 'aabenraa',
 'aac',
 'aachen',
 'aadara',
 'aadhar',
 'aadmi',
 'aadvantag',
 'aae',
 'aaeeb',
 'aaf',
 'aag',
 'aah',
 'aahhh',
 'aaib',
 'aaidh',
 'aaii',
 'aaima',
 'aaingr',
 'aaj',
 'aaja',
 'aakar',
 'aakhri',
 'aakr',
 'aaliya',
 'aaliyah',
 'aall',
 'aalto',
 'aaluijqn',
 'aam',
 'aamaq',
 'aamer',
 'aamon',
 'aand',
 'aangeklaagd',
 'aangenomen',
 'aangezien',
 'aankhen',
 'aankomst',
 'aankondig',
 'aankondigd',
 'aannemen',
 'aanstaand',
 'aantreden',
 'aanval',
 'aanwezigheid',
 'aanzien',
 'aaojejptci',
 'aap',
 'aapk',
 'aapko',
 'aapl',
 'aapn',
 'aaps',
 'aar',
 'aard',
 'aardbevingen',
 'aardvark',
 'aargh',
 'aarhu',
 'aarizonian',
 'aaronkleinshow',
 'aarp',
 'aashiq',
 'aashton',
 'aasif',
 'aata',
 'aau',
 'aaup',
 'aav',
 'aay',
 'aayush',
 'aba',
 'abaaoud',
 'ababa',
 'abacu',
 'abad',
 'abadam',
 'abadgaran',
 'abadi',
 'abagi',
 'abajo',
 'abalada'

In [148]:
df = pd.DataFrame(pd.Series(token_list),columns=['term'])
df['t_index'] = df.index
df['df'] = 0
df['tf'] = 0
df = df[['t_index','term','df','tf']]
df

t_index                  term  df  tf
0             0                   aaa   0   0
1             1                aaaaah   0   0
2             2               aaaaggg   0   0
3             3               aaaahhh   0   0
4             4                  aaah   0   0
5             5                aaahhh   0   0
6             6               aaajiao   0   0
7             7                 aaani   0   0
8             8                aaargh   0   0
9             9                   aab   0   0
10           10                  aabb   0   0
11           11              aabenraa   0   0
12           12                   aac   0   0
13           13                aachen   0   0
14           14                aadara   0   0
15           15                aadhar   0   0
16           16                 aadmi   0   0
17           17             aadvantag   0   0
18           18                   aae   0   0
19           19                 aaeeb   0   0
20           20                   aaf   0   0
21           21                   aag   0   0
22           22                   aah   0   0
23           23                 aahhh   0   0
24           24                  aaib   0   0
25           25                 aaidh   0   0
26           26                  aaii   0   0
27           27                 aaima   0   0
28           28                aaingr   0   0
29           29                   aaj   0   0
...         ...                   ...  ..  ..
117718   117718                   zwo   0   0
117719   117719         zwolenkiewicz   0   0
117720   117720            zwolennici   0   0
117721   117721          zwolennikami   0   0
117722   117722                 zwoll   0   0
117723   117723              zwozdiak   0   0
117724   117724                zwroci   0   0
117725   117725                zwrotu   0   0
117726   117726                 zwvgl   0   0
117727   117727             zwxqtixrl   0   0
117728   117728                 zwyci   0   0
117729   117729                 zwzqj   0   0
117730   117730                   zxh   0   0
117731   117731                  zxpw   0   0
117732   117732                   zxr   0   0
117733   117733                  zxua   0   0
117734   117734            zxycmwjdxj   0   0
117735   117735                zyaira   0   0
117736   117736             zyaratgah   0   0
117737   117737     zybvwqhlbctginctv   0   0
117738   117738              zygankow   0   0
117739   117739                 zygar   0   0
117740   117740  zylinderkopfdichtung   0   0
117741   117741                 zynga   0   0
117742   117742                zytiga   0   0
117743   117743                zytsov   0   0
117744   117744              zyuganov   0   0
117745   117745                   zyz   0   0
117746   117746                   zzz   0   0
117747   117747                  zzzz   0   0

[117748 rows x 4 columns]

In [149]:
# unwanted = ['', u'', None, []]
for news in tqdm(token_df):
    news_li = news.split(' ')
    news_li = dict(Counter(news_li))
#     newdict = {k: v for k, v in news_li.items() if not any([k is i for i in unwanted])}
    keys = list(news_li)
    values = list(news_li.values())
    kkk= df['term'].isin(keys)
    kk = df.loc[kkk,'tf']
    kk = kk.reset_index().index.tolist()
    df.loc[kkk,'tf']=df.loc[kkk,'tf']+np.array(values)[kk]
#     news_li = list(set(news.split(' ')))
    df.loc[kkk,'df'] = df.loc[kkk,'df'] + 1
#     for term in token_list:
#         if token in news:
#             df.loc[df['term']==term,'df'] += 1
df


  5%|▌         | 2556/46590 [00:32<09:14, 79.48it/s]


 11%|█         | 5086/46590 [01:03<08:41, 79.53it/s]


 16%|█▋        | 7605/46590 [01:35<08:10, 79.40it/s]


 22%|██▏       | 10136/46590 [02:07<07:38, 79.43it/s]


 27%|██▋       | 12613/46590 [02:38<07:07, 79.43it/s]


...

 87%|████████▋ | 40548/46590 [08:21<01:14, 80.86it/s]


 93%|█████████▎| 43139/46590 [08:52<00:42, 81.05it/s]


 98%|█████████▊| 45724/46590 [09:22<00:10, 81.22it/s]


100%|██████████| 46590/46590 [09:33<00:00, 81.29it/s]

t_index                  term  df  tf
0             0                   aaa  26  87
1             1                aaaaah   1   1
2             2               aaaaggg   2  34
3             3               aaaahhh   1   1
4             4                  aaah   4  20
5             5                aaahhh   2   2
6             6               aaajiao   1  21
7             7                 aaani   1   1
8             8                aaargh   1   8
9             9                   aab   9  15
10           10                  aabb   1   1
11           11              aabenraa   2   8
12           12                   aac   2   2
13           13                aachen   3   4
14           14                aadara   1   2
15           15                aadhar   1   1
16           16                 aadmi   5  43
17           17             aadvantag   1   2
18           18                   aae   2   2
19           19                 aaeeb   2   2
20           20                   aaf   1   1
21           21                   aag   1   2
22           22                   aah   5  25
23           23                 aahhh   1   2
24           24                  aaib   4   6
25           25                 aaidh   1   1
26           26                  aaii   2   4
27           27                 aaima   1   1
28           28                aaingr   8  18
29           29                   aaj   3  15
...         ...                   ...  ..  ..
117718   117718                   zwo   2   2
117719   117719         zwolenkiewicz   1   1
117720   117720            zwolennici   2   2
117721   117721          zwolennikami   2   2
117722   117722                 zwoll   1   2
117723   117723              zwozdiak   2   2
117724   117724                zwroci   2   2
117725   117725                zwrotu   2   2
117726   117726                 zwvgl   8   8
117727   117727             zwxqtixrl   2   2
117728   117728                 zwyci   2   2
117729   117729                 zwzqj   2   2
117730   117730                   zxh   2   2
117731   117731                  zxpw   2   2
117732   117732                   zxr   2   2
117733   117733                  zxua   8   8
117734   117734            zxycmwjdxj   2   2
117735   117735                zyaira   1   1
117736   117736             zyaratgah   1   1
117737   117737     zybvwqhlbctginctv   8  12
117738   117738              zygankow   2   2
117739   117739                 zygar   2   2
117740   117740  zylinderkopfdichtung   2   2
117741   117741                 zynga   1   1
117742   117742                zytiga   1   1
117743   117743                zytsov   2   2
117744   117744              zyuganov  10  10
117745   117745                   zyz   4   4
117746   117746                   zzz   2   2
117747   117747                  zzzz   1   1

[117748 rows x 4 columns]

In [152]:
df2 = df.drop(df[df.df<3].index) #小於最小類別數目
df2 = df2.drop(df2[df2.df>1375].index) #0.99%
df2.reset_index(drop=True,inplace=True)
df2['t_index'] = df2.index + 1
df2.to_csv('output/dictionary.csv',index=False,header=True)
df2

t_index               term    df    tf
0            1                aaa    26    87
1            2               aaah     4    20
2            3                aab     9    15
3            4             aachen     3     4
4            5              aadmi     5    43
5            6                aah     5    25
6            7               aaib     4     6
7            8             aaingr     8    18
8            9                aaj     3    15
9           10           aaluijqn     8    21
10          11                aam     7    62
11          12              aamaq     4    67
12          13              aamer     3    33
13          14               aand     6     6
14          15         aaojejptci     8    23
15          16                aap    22   104
16          17                aar     4     7
17          18           aardvark     3     5
18          19     aaronkleinshow    58   216
19          20               aarp    26    43
20          21                aba    30   281
21          22              ababa    17   197
22          23              abadi    62   180
23          24             abalon     6    26
24          25               aban     3    81
25          26            abandon  1134  5587
26          27         abandonado     9   107
27          28          abandonar     6    38
28          29            abanico     4    10
29          30               abas     3     9
...        ...                ...   ...   ...
50067    50068          zurbuchen     3     3
50068    50069             zurich    26    28
50069    50070            zurrars     4     4
50070    50071           zusammen    16    18
50071    50072     zusammenarbeit     9    11
50072    50073          zuschauer     8     8
50073    50074               zust     7     7
50074    50075            zustand     6     6
50075    50076              zuvor     8     8
50076    50077   zvcmjsxbppcyrffw     8     8
50077    50078             zvezda    12    14
50078    50079             zvulun     3     3
50079    50080                zvz     4     4
50080    50081            zwanzig     6     6
50081    50082               zwar    20    24
50082    50083              zweck     4     4
50083    50084               zwei    43    43
50084    50085            zweifel     3     3
50085    50086              zweit     6     8
50086    50087            zweiten    10    10
50087    50088            zweiter     5     5
50088    50089              zwick     5     5
50089    50090            zwicker     3     3
50090    50091           zwischen    39    41
50091    50092        zwischenfal     3     3
50092    50093              zwvgl     8     8
50093    50094               zxua     8     8
50094    50095  zybvwqhlbctginctv     8    12
50095    50096           zyuganov    10    10
50096    50097                zyz     4     4

[50097 rows x 4 columns]

tfidf

In [158]:
df2['avg_tfidf']=0
df2

t_index               term    df    tf  avg_tfidf
0            1                aaa    26    87          0
1            2               aaah     4    20          0
2            3                aab     9    15          0
3            4             aachen     3     4          0
4            5              aadmi     5    43          0
5            6                aah     5    25          0
6            7               aaib     4     6          0
7            8             aaingr     8    18          0
8            9                aaj     3    15          0
9           10           aaluijqn     8    21          0
10          11                aam     7    62          0
11          12              aamaq     4    67          0
12          13              aamer     3    33          0
13          14               aand     6     6          0
14          15         aaojejptci     8    23          0
15          16                aap    22   104          0
16          17                aar     4     7          0
17          18           aardvark     3     5          0
18          19     aaronkleinshow    58   216          0
19          20               aarp    26    43          0
20          21                aba    30   281          0
21          22              ababa    17   197          0
22          23              abadi    62   180          0
23          24             abalon     6    26          0
24          25               aban     3    81          0
25          26            abandon  1134  5587          0
26          27         abandonado     9   107          0
27          28          abandonar     6    38          0
28          29            abanico     4    10          0
29          30               abas     3     9          0
...        ...                ...   ...   ...        ...
50067    50068          zurbuchen     3     3          0
50068    50069             zurich    26    28          0
50069    50070            zurrars     4     4          0
50070    50071           zusammen    16    18          0
50071    50072     zusammenarbeit     9    11          0
50072    50073          zuschauer     8     8          0
50073    50074               zust     7     7          0
50074    50075            zustand     6     6          0
50075    50076              zuvor     8     8          0
50076    50077   zvcmjsxbppcyrffw     8     8          0
50077    50078             zvezda    12    14          0
50078    50079             zvulun     3     3          0
50079    50080                zvz     4     4          0
50080    50081            zwanzig     6     6          0
50081    50082               zwar    20    24          0
50082    50083              zweck     4     4          0
50083    50084               zwei    43    43          0
50084    50085            zweifel     3     3          0
50085    50086              zweit     6     8          0
50086    50087            zweiten    10    10          0
50087    50088            zweiter     5     5          0
50088    50089              zwick     5     5          0
50089    50090            zwicker     3     3          0
50090    50091           zwischen    39    41          0
50091    50092        zwischenfal     3     3          0
50092    50093              zwvgl     8     8          0
50093    50094               zxua     8     8          0
50094    50095  zybvwqhlbctginctv     8    12          0
50095    50096           zyuganov    10    10          0
50096    50097                zyz     4     4          0

[50097 rows x 5 columns]

In [173]:
np.array(values)[kk]/sum(np.array(values)[kk]) * np.log10(46590 / df2.df)

array([0.12731707, 0.04243902, 0.10609756, 0.21219512, 0.14853659,
       0.10609756, 0.29707317, 0.10609756, 0.10609756, 0.04243902,
       0.04243902, 0.02121951, 0.02121951, 0.02121951, 0.02121951,
       0.04243902, 0.02121951, 0.04243902, 0.02121951, 0.02121951,
       0.02121951, 0.02121951, 0.02121951, 0.02121951, 0.02121951,
       0.02121951, 0.02121951, 0.02121951, 0.08487805, 0.06365854,
       0.06365854, 0.02121951, 0.12731707, 0.04243902, 0.02121951,
       0.06365854, 0.1697561 , 0.06365854, 0.06365854, 0.1697561 ,
       0.04243902, 0.10609756, 0.02121951, 0.02121951, 0.02121951,
       0.10609756, 0.02121951, 0.04243902, 0.02121951, 0.02121951,
       0.10609756, 0.04243902, 0.14853659, 0.02121951, 0.1697561 ,
       0.08487805, 0.04243902, 0.10609756, 0.02121951, 0.02121951,
       0.06365854, 0.02121951, 0.04243902, 0.02121951, 0.02121951,
       0.02121951, 0.02121951, 0.02121951, 0.04243902, 0.02121951,
       0.02121951, 0.04243902, 0.02121951, 0.04243902, 0.02121

In [174]:
for news in tqdm(token_df):
    news_li = news[:-1].split(' ')
    news_li = dict(Counter(news_li))
#     newdict = {k: v for k, v in news_li.items() if not any([k is i for i in unwanted])}
    keys = list(news_li)
    values = list(news_li.values())
#     all_term_sum = sum(list(news_li.values()))
    kkk= df2['term'].isin(keys)
    kk = df2.loc[kkk].reset_index().index.tolist()
    df2.loc[kkk,'avg_tfidf']+= np.array(values)[kk]/sum(np.array(values)[kk])* np.log10(46590 / df2.loc[kkk,'df'])
df2['avg_tfidf'] /= df2.df
df2


 11%|█▏        | 5335/46590 [00:29<03:50, 178.90it/s]


 23%|██▎       | 10634/46590 [00:59<03:21, 178.48it/s]


 34%|███▍      | 15894/46590 [01:28<02:51, 178.66it/s]


 45%|████▌     | 21180/46590 [01:58<02:22, 178.93it/s]


 57%|█████▋    | 26505/46590 [02:27<01:52, 179.28it/s]


 68%|██████▊   | 31827/46590 [02:57<01:22, 179.48it/s]


 80%|████████  | 37319/46590 [03:26<00:51, 180.49it/s]


 92%|█████████▏| 42835/46590 [03:56<00:20, 181.50it/s]


100%|██████████| 46590/46590 [04:15<00:00, 182.04it/s]

t_index               term    df    tf  avg_tfidf
0            1                aaa    26    87   0.182769
1            2               aaah     4    20   0.249628
2            3                aab     9    15   0.234204
3            4             aachen     3     4   0.023143
4            5              aadmi     5    43   0.192422
5            6                aah     5    25   0.025174
6            7               aaib     4     6   0.018656
7            8             aaingr     8    18   0.010166
8            9                aaj     3    15   0.020421
9           10           aaluijqn     8    21   0.011743
10          11                aam     7    62   0.128639
11          12              aamaq     4    67   0.069105
12          13              aamer     3    33   0.130002
13          14               aand     6     6   0.143078
14          15         aaojejptci     8    23   0.012795
15          16                aap    22   104   0.108272
16          17                aar     4     7   0.017193
17          18           aardvark     3     5   0.060843
18          19     aaronkleinshow    58   216   0.063406
19          20               aarp    26    43   0.338826
20          21                aba    30   281   0.125657
21          22              ababa    17   197   0.039948
22          23              abadi    62   180   0.049666
23          24             abalon     6    26   0.153078
24          25               aban     3    81   0.175633
25          26            abandon  1134  5587   0.022394
26          27         abandonado     9   107   0.126640
27          28          abandonar     6    38   0.155225
28          29            abanico     4    10   0.006090
29          30               abas     3     9   0.099484
...        ...                ...   ...   ...        ...
50067    50068          zurbuchen     3     3   0.067227
50068    50069             zurich    26    28   0.034899
50069    50070            zurrars     4     4   0.007295
50070    50071           zusammen    16    18   0.006953
50071    50072     zusammenarbeit     9    11   0.007152
50072    50073          zuschauer     8     8   0.023947
50073    50074               zust     7     7   0.013135
50074    50075            zustand     6     6   0.016453
50075    50076              zuvor     8     8   0.028983
50076    50077   zvcmjsxbppcyrffw     8     8   0.004907
50077    50078             zvezda    12    14   0.043985
50078    50079             zvulun     3     3   0.027075
50079    50080                zvz     4     4   0.082380
50080    50081            zwanzig     6     6   0.008273
50081    50082               zwar    20    24   0.019203
50082    50083              zweck     4     4   0.003973
50083    50084               zwei    43    43   0.012543
50084    50085            zweifel     3     3   0.006881
50085    50086              zweit     6     8   0.009531
50086    50087            zweiten    10    10   0.008805
50087    50088            zweiter     5     5   0.018864
50088    50089              zwick     5     5   0.022427
50089    50090            zwicker     3     3   0.004107
50090    50091           zwischen    39    41   0.012584
50091    50092        zwischenfal     3     3   0.017776
50092    50093              zwvgl     8     8   0.004907
50093    50094               zxua     8     8   0.004907
50094    50095  zybvwqhlbctginctv     8    12   0.004907
50095    50096           zyuganov    10    10   0.015013
50096    50097                zyz     4     4   0.058039

[50097 rows x 5 columns]

In [179]:
df2.to_csv('output/dictionary.csv',index=False,header=True)

In [178]:
df2.avg_tfidf.mean() , df2.avg_tfidf.min() , df2.avg_tfidf.quantile(0.5)

(0.04428678507782849, 0.0007914636154535665, 0.026634017882596506)

### feature selection

In [226]:
# df1_ = df1.drop(df1.loc[df1['label']=='bs'].index,axis=0)
# df1_ = df1_.drop(df1_.loc[df1_['label']=='half-true'].index,axis=0)
# df1_ = df1_.drop(df1_.loc[df1_['label']=='mostly-true'].index,axis=0)
# df1_ = df1_.drop(df1_.loc[df1_['label']=='barely-true'].index,axis=0)
# df1_.loc[df1_['label']=='0','label'] = 'true'
# df1_.loc[df1_['label']=='1','label'] = 'fake'
# df1_.loc[df1_['label']=='false','label'] = 'fake'
# df1_.loc[df1_['label']=='pants-fire','label'] = 'fake'
# df1_.reset_index(inplace=True,drop=True)

# df1_.to_csv('data/feature_selection_input.csv',index=False)
df1_ = pd.read_csv('data/feature_selection_input.csv')
print(df1_.label.unique())
df1_

['fake' 'true' 'bias' 'conspiracy' 'satire' 'hate' 'junksci' 'state']


text label
0      hous dem aid comey letter jason chaffetz tweet...  fake
1      feel life circl roundabout head straight line ...  true
2      truth octob tension intellig analyst polit pol...  fake
3      video civilian kill singl airstrik identifi ra...  fake
4      print iranian woman sentenc year prison iran r...  fake
5      tri time jacki mason voic reason week exclus c...  true
6      wonder britain icon pop pianist long flight pi...  fake
7      pari franc chose idealist tradit candid sunday...  true
8      donald j trump schedul make highli anticip vis...  true
9      week michael flynn resign nation secur advis s...  true
10     organ action activist group morph barack obama...  true
11     bbc produc spoof real housew tv programm comed...  true
12     mysteri surround reich nazi germani subject de...  fake
13     clinton campaign demand fbi affirm trump russi...  fake
14     ye paid govern troll social media blog forum w...  fake
15     guillermo barro schelotto argentin player set ...  true
16     scandal engulf fargo toppl chairman chief exec...  true
17     caddo nation tribal leader freed spend day bar...  fake
18     fbi close hillari post home headlin world news...  fake
19     wednesday donald trump press confer trump towe...  true
20     email donald trump enter elect year ago singl ...  fake
21     screenwrit ryan murphi produc fx seri american...  true
22     sunday msnbc joy actor director rob reiner acc...  true
23     massachusett cop wife bust pin fake home invas...  fake
24     order abort pill women seven latin american co...  true
25     email histor unit nation committe vote thursda...  fake
26     jerusalem islam state sympath milit celebr nig...  true
27     humili hillari tri hide camera caught min rall...  fake
28     andrea tantaro fox news host charg lawsuit fil...  true
29     hillari clinton sat hideaway studi ceremoni of...  true
...                                                  ...   ...
27884  say democrat told cathol church theyll use fed...  fake
27885  foreign chines prostitut money allegedli group...  fake
27886  say unlik tim kain investedin educ indiana gov...  fake
27887  obamacar provis allow forcedhom inspect govern...  fake
27888  kept congress fulli inform effort creat legal ...  fake
27889  approxim percent colleg grade today increas pe...  true
27890  elimin delta air line jet fuel tax break viola...  true
27891  say statewid elect offici speak favor feder gu...  true
27892  obama administr major rule clinton administr b...  true
27893                                      cuba embargo   fake
27894          say democrat parti creat plan parenthood   fake
27895                       health care offer insur dog   fake
27896            heroin come unit state southern border   true
27897  say ron saunder choic stand rick scott expand ...  fake
27898            barack obama pledg reduc size militari   fake
27899  larg major public oppos major chang medicar fa...  true
27900                         fidel castro endors obama   fake
27901  say spend fiscal budget lower spend fiscal bud...  true
27902  statist evid bail bond increas likelihood awai...  fake
27903            spend defens depart dollar afghanistan   true
27904  republican parti fought hard civil right pass ...  true
27905  major climat chang sponsor sen john kerri joe ...  fake
27906                          ohio credit rate high aa   fake
27907               say day special session cost taxpay   fake
27908                     exclud lobbyist policymak job   fake
27909                     say georg flinn schedul forum   fake
27910                           support surg argu stage   fake
27911  past year democrat spent money countri spent y...  fake
27912  john mccain georg bush absolut plan univers he...  true
27913  new poll percent support presid plan reform he...  fake

[27914 rows x 2 columns]

In [382]:
df1_

text label
0      hous dem aid comey letter jason chaffetz tweet...  fake
1      feel life circl roundabout head straight line ...  true
2      truth octob tension intellig analyst polit pol...  fake
3      video civilian kill singl airstrik identifi ra...  fake
4      print iranian woman sentenc year prison iran r...  fake
5      tri time jacki mason voic reason week exclus c...  true
6      wonder britain icon pop pianist long flight pi...  fake
7      pari franc chose idealist tradit candid sunday...  true
8      donald j trump schedul make highli anticip vis...  true
9      week michael flynn resign nation secur advis s...  true
10     organ action activist group morph barack obama...  true
11     bbc produc spoof real housew tv programm comed...  true
12     mysteri surround reich nazi germani subject de...  fake
13     clinton campaign demand fbi affirm trump russi...  fake
14     ye paid govern troll social media blog forum w...  fake
15     guillermo barro schelotto argentin player set ...  true
16     scandal engulf fargo toppl chairman chief exec...  true
17     caddo nation tribal leader freed spend day bar...  fake
18     fbi close hillari post home headlin world news...  fake
19     wednesday donald trump press confer trump towe...  true
20     email donald trump enter elect year ago singl ...  fake
21     screenwrit ryan murphi produc fx seri american...  true
22     sunday msnbc joy actor director rob reiner acc...  true
23     massachusett cop wife bust pin fake home invas...  fake
24     order abort pill women seven latin american co...  true
25     email histor unit nation committe vote thursda...  fake
26     jerusalem islam state sympath milit celebr nig...  true
27     humili hillari tri hide camera caught min rall...  fake
28     andrea tantaro fox news host charg lawsuit fil...  true
29     hillari clinton sat hideaway studi ceremoni of...  true
...                                                  ...   ...
27884  say democrat told cathol church theyll use fed...  fake
27885  foreign chines prostitut money allegedli group...  fake
27886  say unlik tim kain investedin educ indiana gov...  fake
27887  obamacar provis allow forcedhom inspect govern...  fake
27888  kept congress fulli inform effort creat legal ...  fake
27889  approxim percent colleg grade today increas pe...  true
27890  elimin delta air line jet fuel tax break viola...  true
27891  say statewid elect offici speak favor feder gu...  true
27892  obama administr major rule clinton administr b...  true
27893                                      cuba embargo   fake
27894          say democrat parti creat plan parenthood   fake
27895                       health care offer insur dog   fake
27896            heroin come unit state southern border   true
27897  say ron saunder choic stand rick scott expand ...  fake
27898            barack obama pledg reduc size militari   fake
27899  larg major public oppos major chang medicar fa...  true
27900                         fidel castro endors obama   fake
27901  say spend fiscal budget lower spend fiscal bud...  true
27902  statist evid bail bond increas likelihood awai...  fake
27903            spend defens depart dollar afghanistan   true
27904  republican parti fought hard civil right pass ...  true
27905  major climat chang sponsor sen john kerri joe ...  fake
27906                          ohio credit rate high aa   fake
27907               say day special session cost taxpay   fake
27908                     exclud lobbyist policymak job   fake
27909                     say georg flinn schedul forum   fake
27910                           support surg argu stage   fake
27911  past year democrat spent money countri spent y...  fake
27912  john mccain georg bush absolut plan univers he...  true
27913  new poll percent support presid plan reform he...  fake

[27914 rows x 2 columns]

In [180]:
# pickle.dump(file=open('data/token_df.pkl','wb'),obj=token_df)
token_df = pickle.load(open('data/token_df.pkl','rb'))
df2 = pd.read_csv('output/dictionary.csv')
ori_df = pd.read_csv('data/combine_data.csv')
# token_df

In [303]:
terms = df2['term'].tolist()
dict_df = df2.filter(['term','avg_tfidf'])
dict_df

term  avg_tfidf
0                    aaa   0.182769
1                   aaah   0.249628
2                    aab   0.234204
3                 aachen   0.023143
4                  aadmi   0.192422
5                    aah   0.025174
6                   aaib   0.018656
7                 aaingr   0.010166
8                    aaj   0.020421
9               aaluijqn   0.011743
10                   aam   0.128639
11                 aamaq   0.069105
12                 aamer   0.130002
13                  aand   0.143078
14            aaojejptci   0.012795
15                   aap   0.108272
16                   aar   0.017193
17              aardvark   0.060843
18        aaronkleinshow   0.063406
19                  aarp   0.338826
20                   aba   0.125657
21                 ababa   0.039948
22                 abadi   0.049666
23                abalon   0.153078
24                  aban   0.175633
25               abandon   0.022394
26            abandonado   0.126640
27             abandonar   0.155225
28               abanico   0.006090
29                  abas   0.099484
...                  ...        ...
50067          zurbuchen   0.067227
50068             zurich   0.034899
50069            zurrars   0.007295
50070           zusammen   0.006953
50071     zusammenarbeit   0.007152
50072          zuschauer   0.023947
50073               zust   0.013135
50074            zustand   0.016453
50075              zuvor   0.028983
50076   zvcmjsxbppcyrffw   0.004907
50077             zvezda   0.043985
50078             zvulun   0.027075
50079                zvz   0.082380
50080            zwanzig   0.008273
50081               zwar   0.019203
50082              zweck   0.003973
50083               zwei   0.012543
50084            zweifel   0.006881
50085              zweit   0.009531
50086            zweiten   0.008805
50087            zweiter   0.018864
50088              zwick   0.022427
50089            zwicker   0.004107
50090           zwischen   0.012584
50091        zwischenfal   0.017776
50092              zwvgl   0.004907
50093               zxua   0.004907
50094  zybvwqhlbctginctv   0.004907
50095           zyuganov   0.015013
50096                zyz   0.058039

[50097 rows x 2 columns]

In [231]:
class_token_dict = dict()
for i in df1_['label'].unique().tolist():
    kk = df1_[df1_['label']== i]
    class_token_dict[i]=kk['text'].tolist()
len(class_token_dict['fake']) , len(class_token_dict)

(13986, 8)

In [246]:
cat = df1_.label.unique().tolist()
cat[c], class_token_dict.keys()

('satire',
 dict_keys(['fake', 'true', 'bias', 'conspiracy', 'satire', 'hate', 'junksci', 'state']))

In [249]:
count = []
for k,v in class_token_dict.items():
    count.append(len(v))
count

[13986, 12440, 443, 430, 146, 246, 102, 121]

In [338]:
df = dict_df.filter(['term'])
# cat = df1_.label.unique().tolist()
df['score_llr'] = 0
df['score_chi'] = 0
df['score_emi'] = 0
for i in tqdm(range(len(class_token_dict))):
    cat_ = df1_.label.unique().tolist()
    c = count[i]
    c_ = sum(count)-c
    df['n11'] = 0
    df['n10'] = 0
    df['n01'] = 0
    df['n00'] = 0
    n11 = dict(Counter(class_token_dict_[cat_[i]]))
    keys = list(n11)
    values = list(n11.values()) 
    kkk= df['term'].isin(keys)
    kk = df.loc[kkk].reset_index().index.tolist()
    df.loc[kkk,'n11']=np.array(values)[kk]
    df['n10'] = c - df['n11']
    cat_.remove(cat_[i])
    n01 = itemgetter(*cat_)(class_token_dict_)
    n01 = sum(list(myvalues),[])
    n01 = dict(Counter(n01))
    keys = list(n01)
    values = list(n01.values())
    kkk= df['term'].isin(keys)
    kk = df.loc[kkk].reset_index().index.tolist()
    df.loc[kkk,'n01']=np.array(values)[kk]
    df['n00'] = c_ - df['n01']
    
    n11 = df['n11'] + 1
    n01 = df['n01'] + 1
    n10 = df['n10'] + 1
    n00 = df['n00'] + 1
    N = df['N'] = n11 + n01 + n10 + n00
    score = (((n11+n01)/N) ** n11) * ((1 - ((n11+n01)/N)) ** n10) * (((n11+n01)/N) ** n01) * ((1 - ((n11+n01)/N)) ** n00)
    score /= (((n11/(n11+n10)) ** n11) * ((1 - (n11/(n11+n10))) ** n10) * ((n01/(n01+n00)) ** n01) * ((1 - (n01/(n01+n00))) ** n00))
    score = -2 * np.log10(score) #LLR
    df['score_llr'] += score
    
    n11 = df['n11'] + 1e-6
    n01 = df['n01'] + 1e-6
    n10 = df['n10'] + 1e-6
    n00 = df['n00'] + 1e-6
    N = df['N'] = n11 + n01 + n10 + n00      
    e11 = N * (n11+n01)/N * (n11+n10)/N #chi-squre
    e10 = N * (n11+n10)/N * (n10+n00)/N
    e01 = N * (n11+n01)/N * (n01+n00)/N
    e00 = N * (n01+n00)/N * (n10+n00)/N
    df['score_chi'] += ((n11-e11)**2)/e11 + ((n10-e10)**2)/e10 + ((n01-e01)**2)/e01 + ((n00-e00)**2)/e00
    
    n11 = df['n11'] + 1e-8
    n01 = df['n01'] + 1e-8
    n10 = df['n10'] + 1e-8
    n00 = df['n00'] + 1e-8
    N = df['N'] = n11 + n01 + n10 + n00   
    
    m11 = (n11/N) * np.log2(((n11/N)/((n11+n01)/N * (n11+n10)/N))) #EMI
    m10 = n10/N * np.log2((n10/N)/((n11+n10)/N * (n10+n00)/N))
    m01 = n01/N * np.log2((n01/N)/((n11+n01)/N * (n01+n00)/N))
    m00 = n00/N * np.log2((n00/N)/((n01+n00)/N * (n10+n00)/N))
    df['score_emi'] += m11 + m10 + m01 + m00
    


df = pd.merge(df,dict_df,on='term',how='inner')
df_ = df.filter(['term','avg_tfidf','score_chi','score_llr','score_emi'])







  0%|          | 0/8 [00:00<?, ?it/s]/home/leoqaz12/.local/lib/python3.6/site-packages/ipykernel/__main__.py:39: RuntimeWarning: divide by zero encountered in log10
/home/leoqaz12/.local/lib/python3.6/site-packages/ipykernel/__main__.py:62: RuntimeWarning: invalid value encountered in log2






 12%|█▎        | 1/8 [00:01<00:08,  1.20s/it]





 25%|██▌       | 2/8 [00:02<00:07,  1.24s/it]





 38%|███▊      | 3/8 [00:03<00:05,  1.13s/it]





 50%|█████     | 4/8 [00:04<00:04,  1.08s/it]





 62%|██████▎   | 5/8 [00:05<00:03,  1.04s/it]





 75%|███████▌  | 6/8 [00:06<00:02,  1.02s/it]





 88%|████████▊ | 7/8 [00:07<00:01,  1.01s/it]





100%|██████████| 8/8 [00:07<00:00,  1.00it/s]







In [339]:
df_

term  avg_tfidf     score_chi  score_llr  score_emi
0                    aaa   0.182769  1.797410e+04        NaN   0.592070
1                   aaah   0.249628  3.563683e+02        NaN   0.012398
2                    aab   0.234204  6.973707e+03        NaN   0.235770
3                 aachen   0.023143  7.511697e+02        NaN   0.022455
4                  aadmi   0.192422  1.981660e+03        NaN   0.057381
5                    aah   0.025174  4.276803e+03        NaN   0.137922
6                   aaib   0.018656  1.076032e+03        NaN   0.038489
7                 aaingr   0.010166  1.072231e+06        NaN        NaN
8                    aaj   0.020421  2.487753e+04        NaN   0.836411
9               aaluijqn   0.011743  3.607681e+04        NaN   1.157366
10                   aam   0.128639  4.232435e+03        NaN   0.117531
11                 aamaq   0.069105  4.999499e+03        NaN   0.164498
12                 aamer   0.130002  3.334030e+03        NaN   0.105459
13                  aand   0.143078  1.290269e+03        NaN   0.048748
14            aaojejptci   0.012795  2.395798e+03        NaN   0.085680
15                   aap   0.108272  1.145338e+04        NaN   0.338008
16                   aar   0.017193  5.387002e+01        NaN   0.002583
17              aardvark   0.060843  5.027609e+02        NaN   0.017325
18        aaronkleinshow   0.063406  8.824214e+03        NaN   0.311488
19                  aarp   0.338826  1.826766e+03        NaN   0.050775
20                   aba   0.125657  6.333761e+03        NaN   0.181319
21                 ababa   0.039948  3.807074e+01        NaN   0.001083
22                 abadi   0.049666  2.762718e+03        NaN   0.076892
23                abalon   0.153078  1.322481e+02        NaN   0.003812
24                  aban   0.175633  1.515304e+03        NaN   0.053068
25               abandon   0.022394  3.515721e+04        NaN   1.106275
26            abandonado   0.126640  4.484244e+03        NaN   0.156173
27             abandonar   0.155225  5.870723e+03        NaN   0.209679
28               abanico   0.006090  4.818794e+02        NaN   0.017665
29                  abas   0.099484  1.559935e+02  86.200322   0.005654
...                  ...        ...           ...        ...        ...
50067          zurbuchen   0.067227  7.256500e+00  18.194559   0.000204
50068             zurich   0.034899  7.785188e-02  15.616460   0.000003
50069            zurrars   0.007295  1.187115e+00  15.749769   0.000042
50070           zusammen   0.006953  1.187115e+00  15.749769   0.000042
50071     zusammenarbeit   0.007152  2.053390e+00  14.246611   0.000075
50072          zuschauer   0.023947  8.578962e-01  15.664109   0.000033
50073               zust   0.013135  6.974011e+00  12.973055   0.000242
50074            zustand   0.016453  4.405452e+00  12.097973   0.000169
50075              zuvor   0.028983  2.053390e+00  14.246611   0.000075
50076   zvcmjsxbppcyrffw   0.004907  1.415893e+01  13.918549   0.000491
50077             zvezda   0.043985  8.578962e-01  15.664109   0.000033
50078             zvulun   0.027075  2.053390e+00  14.246611   0.000075
50079                zvz   0.082380  1.805179e+01  15.958817   0.000227
50080            zwanzig   0.008273  2.053390e+00  14.246611   0.000075
50081               zwar   0.019203  2.053390e+00  14.246611   0.000075
50082              zweck   0.003973  8.578962e-01  15.664109   0.000033
50083               zwei   0.012543  8.741470e+00  13.031480   0.000303
50084            zweifel   0.006881  6.161154e+00  12.109831   0.000226
50085              zweit   0.009531  1.745276e+01  14.223983   0.000608
50086            zweiten   0.008805  4.107113e+00  12.738523   0.000151
50087            zweiter   0.018864  1.053287e+01  13.227324   0.000364
50088              zwick   0.022427  4.932452e-01  13.991948   0.000016
50089            zwicker   0.004107  1.553891e+00  16.111569   0.000042
50090           zwischen   0.012584  7.165561e+00  12.466570

In [350]:
threshold_tfidf = np.min(df_['avg_tfidf']) #1.45=>502 數字大嚴格
threshold_chi = np.min(df_['score_chi']) #1=>350
threshold_llr = np.min(df_['score_llr']) #1.75=>543
threshold_emi = np.min(df_['score_emi']) #1.75=>543
print(threshold_tfidf,threshold_chi,threshold_llr,threshold_emi)

0.0007914636154535665 0.0004595267692442124 1.9688646933055802 1.090534589497743e-11


In [351]:
df_t = df_[df_['avg_tfidf']>threshold_tfidf]
df_t = df_t[df_t['score_chi']>threshold_chi]
df_t = df_t[df_t['score_llr']>threshold_llr]
df_t = df_t[df_t['score_emi']>threshold_emi]
df_t.reset_index(inplace=True,drop=True)
df_t.to_csv('output/feature_selection_score.csv',index=False)
df_t

term  avg_tfidf    score_chi   score_llr  score_emi
0                   abas   0.099484   155.993473   86.200322   0.005654
1         abfalecbaldwin   0.029319    15.183392   13.546114   0.000533
2                abruzzo   0.063948     8.483806   12.147326   0.000310
3                  adein   0.139249    13.797262   13.932033   0.000462
4                 adumim   0.043406     1.082041   15.765851   0.000039
5                aesthet   0.046593  3569.304335  224.859569   0.012974
6                aggrand   0.043265   151.794374   33.957928   0.001889
7            agonizingli   0.024795    94.692541   49.010634   0.003163
8                   ahab   0.053316    79.428863   41.885202   0.002790
9                  ahora   0.049325    84.898446   42.727803   0.002329
10            ahqqtpghax   0.034348   115.372529   60.728623   0.003996
11                   aht   0.078930    36.749853   21.489273   0.001416
12                aktion   0.020022    22.208308   23.713900   0.000695
13                 aktiv   0.054941    69.798535   52.758974   0.002372
14                alarma   0.218211   135.200731   74.316056   0.004891
15               alcanza   0.053515    70.992452   42.279030   0.002192
16                alchem   0.043340    26.147420   16.864874   0.000923
17               aldridg   0.027992   129.195314   83.282565   0.004181
18                aliado   0.073178    83.890326   44.336045   0.002965
19               alibaba   0.067955    44.643570   34.443733   0.001346
20                  alim   0.064467    70.981440   43.093359   0.002146
21             aljazeera   0.041574    19.545895   14.586794   0.000690
22               alkohol   0.068641    87.802728   60.323226   0.002932
23                allein   0.058510    31.065275   18.723625   0.001169
24                 allig   0.200854  1338.671086   88.152234   0.004810
25                allora   0.091033    44.973676   25.517509   0.001717
26                almsot   0.014896    47.279278   32.040682   0.001460
27                alumna   0.037695    26.424230   17.094090   0.000932
28                  amal   0.043904  2688.294153  132.331369   0.007057
29                amargo   0.077401    40.436743   22.834379   0.001428
...                  ...        ...          ...         ...        ...
41301          zurbuchen   0.067227     7.256500   18.194559   0.000204
41302             zurich   0.034899     0.077852   15.616460   0.000003
41303            zurrars   0.007295     1.187115   15.749769   0.000042
41304           zusammen   0.006953     1.187115   15.749769   0.000042
41305     zusammenarbeit   0.007152     2.053390   14.246611   0.000075
41306          zuschauer   0.023947     0.857896   15.664109   0.000033
41307               zust   0.013135     6.974011   12.973055   0.000242
41308            zustand   0.016453     4.405452   12.097973   0.000169
41309              zuvor   0.028983     2.053390   14.246611   0.000075
41310   zvcmjsxbppcyrffw   0.004907    14.158934   13.918549   0.000491
41311             zvezda   0.043985     0.857896   15.664109   0.000033
41312             zvulun   0.027075     2.053390   14.246611   0.000075
41313                zvz   0.082380    18.051787   15.958817   0.000227
41314            zwanzig   0.008273     2.053390   14.246611   0.000075
41315               zwar   0.019203     2.053390   14.246611   0.000075
41316              zweck   0.003973     0.857896   15.664109   0.000033
41317               zwei   0.012543     8.741470   13.031480   0.000303
41318            zweifel   0.006881     6.161154   12.109831   0.000226
41319              zweit   0.009531    17.452763   14.223983   0.000608
41320            zweiten   0.008805     4.107113   12.738523   0.000151
41321            zweiter   0.018864    10.532872   13.227324   0.000364
41322              zwick   0.022427     0.493245   13.991948   0.000016
41323            zwicker   0.004107     1.553891   16.111569   0.000042
41324           zwischen   0.012584     7.165561   12.466570

build dict

In [373]:
dict_df3 = pd.read_csv('output/feature_selection_score.csv',index_col=None)
threshold_tfidf = np.mean(dict_df3['avg_tfidf'])+0*np.std(dict_df3['avg_tfidf']) #1.45=>502 數字大嚴格
threshold_chi = np.mean(dict_df3['score_chi'])+0*np.std(dict_df3['score_chi']) #1=>350
threshold_llr = np.mean(dict_df3['score_llr'])+0*np.std(dict_df3['score_llr']) #1.75=>543
threshold_emi = np.mean(dict_df3['score_emi'])+0*np.std(dict_df3['score_emi']) #1.75=>543
dict_df3['vote'] = 0
dict_df3

term  avg_tfidf    score_chi   score_llr  score_emi  vote
0                   abas   0.099484   155.993473   86.200322   0.005654     0
1         abfalecbaldwin   0.029319    15.183392   13.546114   0.000533     0
2                abruzzo   0.063948     8.483806   12.147326   0.000310     0
3                  adein   0.139249    13.797262   13.932033   0.000462     0
4                 adumim   0.043406     1.082041   15.765851   0.000039     0
5                aesthet   0.046593  3569.304335  224.859569   0.012974     0
6                aggrand   0.043265   151.794374   33.957928   0.001889     0
7            agonizingli   0.024795    94.692541   49.010634   0.003163     0
8                   ahab   0.053316    79.428863   41.885202   0.002790     0
9                  ahora   0.049325    84.898446   42.727803   0.002329     0
10            ahqqtpghax   0.034348   115.372529   60.728623   0.003996     0
11                   aht   0.078930    36.749853   21.489273   0.001416     0
12                aktion   0.020022    22.208308   23.713900   0.000695     0
13                 aktiv   0.054941    69.798535   52.758974   0.002372     0
14                alarma   0.218211   135.200731   74.316056   0.004891     0
15               alcanza   0.053515    70.992452   42.279030   0.002192     0
16                alchem   0.043340    26.147420   16.864874   0.000923     0
17               aldridg   0.027992   129.195314   83.282565   0.004181     0
18                aliado   0.073178    83.890326   44.336045   0.002965     0
19               alibaba   0.067955    44.643570   34.443733   0.001346     0
20                  alim   0.064467    70.981440   43.093359   0.002146     0
21             aljazeera   0.041574    19.545895   14.586794   0.000690     0
22               alkohol   0.068641    87.802728   60.323226   0.002932     0
23                allein   0.058510    31.065275   18.723625   0.001169     0
24                 allig   0.200854  1338.671086   88.152234   0.004810     0
25                allora   0.091033    44.973676   25.517509   0.001717     0
26                almsot   0.014896    47.279278   32.040682   0.001460     0
27                alumna   0.037695    26.424230   17.094090   0.000932     0
28                  amal   0.043904  2688.294153  132.331369   0.007057     0
29                amargo   0.077401    40.436743   22.834379   0.001428     0
...                  ...        ...          ...         ...        ...   ...
41301          zurbuchen   0.067227     7.256500   18.194559   0.000204     0
41302             zurich   0.034899     0.077852   15.616460   0.000003     0
41303            zurrars   0.007295     1.187115   15.749769   0.000042     0
41304           zusammen   0.006953     1.187115   15.749769   0.000042     0
41305     zusammenarbeit   0.007152     2.053390   14.246611   0.000075     0
41306          zuschauer   0.023947     0.857896   15.664109   0.000033     0
41307               zust   0.013135     6.974011   12.973055   0.000242     0
41308            zustand   0.016453     4.405452   12.097973   0.000169     0
41309              zuvor   0.028983     2.053390   14.246611   0.000075     0
41310   zvcmjsxbppcyrffw   0.004907    14.158934   13.918549   0.000491     0
41311             zvezda   0.043985     0.857896   15.664109   0.000033     0
41312             zvulun   0.027075     2.053390   14.246611   0.000075     0
41313                zvz   0.082380    18.051787   15.958817   0.000227     0
41314            zwanzig   0.008273     2.053390   14.246611   0.000075     0
41315               zwar   0.019203     2.053390   14.246611   0.000075     0
41316              zweck   0.003973     0.857896   15.664109   0.000033     0
41317               zwei   0.012543     8.741470   13.031480   0.000303     0
41318            zweifel   0.006881     6.161154   12.109831   0.000226     0
41319              zweit   0.009531    17.452763   14.223983   0.000608     0
41320            zweiten   0.008805     4.

In [374]:
df1 = dict_df3[dict_df3['avg_tfidf']>threshold_tfidf]
df2 = dict_df3[dict_df3['score_chi']>threshold_chi]
df3 = dict_df3[dict_df3['score_llr']>threshold_llr]
df4 = dict_df3[dict_df3['score_emi']>threshold_emi]
# dict_df3

dict_df3.loc[df1.index,'vote'] +=1
dict_df3.loc[df2.index,'vote'] +=1
dict_df3.loc[df3.index,'vote'] +=1
dict_df3.loc[df4.index,'vote'] +=1
dict_df3

term  avg_tfidf    score_chi   score_llr  score_emi  vote
0                   abas   0.099484   155.993473   86.200322   0.005654     2
1         abfalecbaldwin   0.029319    15.183392   13.546114   0.000533     0
2                abruzzo   0.063948     8.483806   12.147326   0.000310     1
3                  adein   0.139249    13.797262   13.932033   0.000462     1
4                 adumim   0.043406     1.082041   15.765851   0.000039     1
5                aesthet   0.046593  3569.304335  224.859569   0.012974     3
6                aggrand   0.043265   151.794374   33.957928   0.001889     2
7            agonizingli   0.024795    94.692541   49.010634   0.003163     1
8                   ahab   0.053316    79.428863   41.885202   0.002790     2
9                  ahora   0.049325    84.898446   42.727803   0.002329     2
10            ahqqtpghax   0.034348   115.372529   60.728623   0.003996     1
11                   aht   0.078930    36.749853   21.489273   0.001416     2
12                aktion   0.020022    22.208308   23.713900   0.000695     0
13                 aktiv   0.054941    69.798535   52.758974   0.002372     2
14                alarma   0.218211   135.200731   74.316056   0.004891     2
15               alcanza   0.053515    70.992452   42.279030   0.002192     2
16                alchem   0.043340    26.147420   16.864874   0.000923     1
17               aldridg   0.027992   129.195314   83.282565   0.004181     1
18                aliado   0.073178    83.890326   44.336045   0.002965     2
19               alibaba   0.067955    44.643570   34.443733   0.001346     2
20                  alim   0.064467    70.981440   43.093359   0.002146     2
21             aljazeera   0.041574    19.545895   14.586794   0.000690     1
22               alkohol   0.068641    87.802728   60.323226   0.002932     2
23                allein   0.058510    31.065275   18.723625   0.001169     2
24                 allig   0.200854  1338.671086   88.152234   0.004810     3
25                allora   0.091033    44.973676   25.517509   0.001717     2
26                almsot   0.014896    47.279278   32.040682   0.001460     1
27                alumna   0.037695    26.424230   17.094090   0.000932     0
28                  amal   0.043904  2688.294153  132.331369   0.007057     3
29                amargo   0.077401    40.436743   22.834379   0.001428     2
...                  ...        ...          ...         ...        ...   ...
41301          zurbuchen   0.067227     7.256500   18.194559   0.000204     1
41302             zurich   0.034899     0.077852   15.616460   0.000003     0
41303            zurrars   0.007295     1.187115   15.749769   0.000042     0
41304           zusammen   0.006953     1.187115   15.749769   0.000042     0
41305     zusammenarbeit   0.007152     2.053390   14.246611   0.000075     0
41306          zuschauer   0.023947     0.857896   15.664109   0.000033     0
41307               zust   0.013135     6.974011   12.973055   0.000242     0
41308            zustand   0.016453     4.405452   12.097973   0.000169     0
41309              zuvor   0.028983     2.053390   14.246611   0.000075     0
41310   zvcmjsxbppcyrffw   0.004907    14.158934   13.918549   0.000491     0
41311             zvezda   0.043985     0.857896   15.664109   0.000033     1
41312             zvulun   0.027075     2.053390   14.246611   0.000075     0
41313                zvz   0.082380    18.051787   15.958817   0.000227     1
41314            zwanzig   0.008273     2.053390   14.246611   0.000075     0
41315               zwar   0.019203     2.053390   14.246611   0.000075     0
41316              zweck   0.003973     0.857896   15.664109   0.000033     0
41317               zwei   0.012543     8.741470   13.031480   0.000303     0
41318            zweifel   0.006881     6.161154   12.109831   0.000226     0
41319              zweit   0.009531    17.452763   14.223983   0.000608     0
41320            zweiten   0.008805     4.

In [378]:
df_vote = dict_df3[dict_df3.vote>2]
df_vote

term  avg_tfidf     score_chi   score_llr  score_emi  vote
5          aesthet   0.046593   3569.304335  224.859569   0.012974     3
24           allig   0.200854   1338.671086   88.152234   0.004810     3
28            amal   0.043904   2688.294153  132.331369   0.007057     3
30       amazingli   0.052369   7108.177285  383.384030   0.022118     3
59     appalachian   0.141023   2877.332812  128.416745   0.007109     3
65            aqsa   0.053808  15268.333383  442.398673   0.025780     3
73            ariz   0.063762    216.126921   34.076112   0.001513     3
74       armadillo   0.122153    999.200422  112.047875   0.006015     3
79           arora   0.049180    186.290606         inf   0.006528     3
103          athol   0.046624    799.015664         inf   0.007855     3
106     attabpress   0.484075    221.168530   42.852529   0.002628     3
121          aureu   0.054905    908.369727   62.080300   0.002979     3
128      autograph   0.044480   1382.116386  161.797920   0.008996     3
153           babi   0.044611  19064.958804         inf   0.054056     3
156       backpack   0.048189   1224.387304  169.164708   0.009571     3
159         badger   0.108495    425.434500   46.378618   0.002463     3
175       bamboozl   0.054573   7150.548905         inf   0.028760     3
185       baphomet   0.068249   1924.703725  112.557802   0.006122     3
197        barmaid   0.054355    288.149905   40.590597   0.001899     3
198      barracuda   0.144526    473.624078   63.058348   0.003473     3
208      basketbal   0.048157   2825.100279  125.228501   0.006798     3
224          beard   0.052478    752.408402  113.903406   0.006130     3
227          beatl   0.045670   4632.093713  294.031408   0.017086     3
246        bellmor   0.123387    730.291094  106.294355   0.006394     3
267         berkan   0.176793    261.438173   52.125415   0.003068     3
272        bernish   0.081934   2348.829949  188.516410   0.011157     3
304           bigg   0.167213    343.996098   40.754863   0.002189     3
318      biodivers   0.048542   7076.730269  328.421123   0.018924     3
342       blackfac   0.057426    587.900501   76.913846   0.004171     3
353         blasio   0.045748    715.463050   69.709912   0.003934     3
...            ...        ...           ...         ...        ...   ...
37123        unarm   0.041408    447.846399   34.637035   0.001171     3
37149  unbeknownst   0.068369   1097.222900   77.735039   0.003814     3
37190      unchang   0.056953   1096.527059   77.392373   0.003797     3
37217    uncompens   0.479889    921.094331   70.599844   0.003603     3
37232  unconstitut   0.071282    850.851635   56.349444   0.002363     3
37321    underpaid   0.098500    909.944432   49.763952   0.002053     3
37418     unemploy   0.213829   1488.858411   58.309433   0.002454     3
37627        unman   0.060042   1406.502488   46.411490   0.001850     3
37927      unviabl   0.071437    448.793647   34.244408   0.001251     3
37929       unwant   0.051146    435.658782   37.116100   0.001224     3
37994       upshot   0.044620    787.746891   41.727489   0.001522     3
38006       uptick   0.059945   1529.880272   55.367204   0.002583     3
38020      uranium   0.058853    478.631565   39.244315   0.001389     3
38191       vaccin   0.073413    224.122362   29.298190   0.001038     3
38225       valdai   0.049546    392.972295   34.332325   0.001452     3
38406         vega   0.041845    464.736867   41.508096   0.001454     3
38436       veliki   0.044037   1022.061817   40.599426   0.001743     3
38502         vera   0.046300    345.136832   33.633033   0.001134     3
38678         veto   0.083648    443.701314   39.732351   0.001428     3
38890     virginia   0.074810    742.544829   45.917472   0.001720     3
38903         viru   0.044433    942.457587   48.654719   0.001856     3
38907         visa   0.053348    603.163488   35.140228   0.001114     3
39270       waiver   0.137969    511.445428   33.932379   0.001063     3

In [379]:
df_vote.reset_index(inplace=True,drop=True)
df_vote.to_csv('output/final_dict_1000.csv',index=False)
df_vote

term  avg_tfidf     score_chi   score_llr  score_emi  vote
0         aesthet   0.046593   3569.304335  224.859569   0.012974     3
1           allig   0.200854   1338.671086   88.152234   0.004810     3
2            amal   0.043904   2688.294153  132.331369   0.007057     3
3       amazingli   0.052369   7108.177285  383.384030   0.022118     3
4     appalachian   0.141023   2877.332812  128.416745   0.007109     3
5            aqsa   0.053808  15268.333383  442.398673   0.025780     3
6            ariz   0.063762    216.126921   34.076112   0.001513     3
7       armadillo   0.122153    999.200422  112.047875   0.006015     3
8           arora   0.049180    186.290606         inf   0.006528     3
9           athol   0.046624    799.015664         inf   0.007855     3
10     attabpress   0.484075    221.168530   42.852529   0.002628     3
11          aureu   0.054905    908.369727   62.080300   0.002979     3
12      autograph   0.044480   1382.116386  161.797920   0.008996     3
13           babi   0.044611  19064.958804         inf   0.054056     3
14       backpack   0.048189   1224.387304  169.164708   0.009571     3
15         badger   0.108495    425.434500   46.378618   0.002463     3
16       bamboozl   0.054573   7150.548905         inf   0.028760     3
17       baphomet   0.068249   1924.703725  112.557802   0.006122     3
18        barmaid   0.054355    288.149905   40.590597   0.001899     3
19      barracuda   0.144526    473.624078   63.058348   0.003473     3
20      basketbal   0.048157   2825.100279  125.228501   0.006798     3
21          beard   0.052478    752.408402  113.903406   0.006130     3
22          beatl   0.045670   4632.093713  294.031408   0.017086     3
23        bellmor   0.123387    730.291094  106.294355   0.006394     3
24         berkan   0.176793    261.438173   52.125415   0.003068     3
25        bernish   0.081934   2348.829949  188.516410   0.011157     3
26           bigg   0.167213    343.996098   40.754863   0.002189     3
27      biodivers   0.048542   7076.730269  328.421123   0.018924     3
28       blackfac   0.057426    587.900501   76.913846   0.004171     3
29         blasio   0.045748    715.463050   69.709912   0.003934     3
...           ...        ...           ...         ...        ...   ...
1233        unarm   0.041408    447.846399   34.637035   0.001171     3
1234  unbeknownst   0.068369   1097.222900   77.735039   0.003814     3
1235      unchang   0.056953   1096.527059   77.392373   0.003797     3
1236    uncompens   0.479889    921.094331   70.599844   0.003603     3
1237  unconstitut   0.071282    850.851635   56.349444   0.002363     3
1238    underpaid   0.098500    909.944432   49.763952   0.002053     3
1239     unemploy   0.213829   1488.858411   58.309433   0.002454     3
1240        unman   0.060042   1406.502488   46.411490   0.001850     3
1241      unviabl   0.071437    448.793647   34.244408   0.001251     3
1242       unwant   0.051146    435.658782   37.116100   0.001224     3
1243       upshot   0.044620    787.746891   41.727489   0.001522     3
1244       uptick   0.059945   1529.880272   55.367204   0.002583     3
1245      uranium   0.058853    478.631565   39.244315   0.001389     3
1246       vaccin   0.073413    224.122362   29.298190   0.001038     3
1247       valdai   0.049546    392.972295   34.332325   0.001452     3
1248         vega   0.041845    464.736867   41.508096   0.001454     3
1249       veliki   0.044037   1022.061817   40.599426   0.001743     3
1250         vera   0.046300    345.136832   33.633033   0.001134     3
1251         veto   0.083648    443.701314   39.732351   0.001428     3
1252     virginia   0.074810    742.544829   45.917472   0.001720     3
1253         viru   0.044433    942.457587   48.654719   0.001856     3
1254         visa   0.053348    603.163488   35.140228   0.001114     3
1255       waiver   0.137969    511.445428   33.932379   0.001063     3
1256       warmer   0.064921    761.207603   33.97828

In [387]:
ori_df

text        label
0      house dem aide we didn t even see comey s lett...            1
1      ever get the feeling your life circles the rou...            0
2      why the truth might get you fired october the ...            1
3      videos civilians killed in single us airstrike...            1
4      print an iranian woman has been sentenced to s...            1
5      in these trying times jackie mason is the voic...            0
6      ever wonder how britain s most iconic pop pian...            1
7      paris france chose an idealistic traditional c...            0
8      donald j trump is scheduled to make a highly a...            0
9      a week before michael t flynn resigned as nati...            0
10     organizing for action the activist group that ...            0
11     the bbc produced spoof on the real housewives ...            0
12     the mystery surrounding the third reich and na...            1
13     clinton campaign demands fbi affirm trump s ru...            1
14     yes there are paid government trolls on social...            1
15     guillermo barros schelotto was not the first a...            0
16     the scandal engulfing wells fargo toppled its ...            0
17     a caddo nation tribal leader has just been fre...            1
18     fbi closes in on hillary posted on home headli...            1
19     wednesday after donald trump s press conferenc...            0
20     email since donald trump entered the election ...            1
21     screenwriter ryan murphy who has produced the ...            0
22     sunday on msnbc s am joy actor and director ro...            0
23     massachusetts cop s wife busted for pinning fa...            1
24     orders for abortion pills by women in seven la...            0
25     email in an historic move the united nations f...            1
26     jerusalem islamic state sympathizers and milit...            0
27     humiliated hillary tries to hide what camera c...            1
28     andrea tantaros a former fox news host charged...            0
29     hillary clinton sat in the hideaway study off ...            0
...                                                  ...          ...
46560  says ron saunders made the choice to stand wit...        false
46561  since president obama took office there are ov...    half-true
46562  people in the top tax bracket these so called ...  barely-true
46563  barack obama has pledged to reduce the size of...        false
46564  large majorities of the public oppose major ch...         true
46565                       fidel castro endorses obama    pants-fire
46566  says spending in the fiscal budget was lower t...         true
46567  there is no statistical evidence that bail bon...        false
46568  household incomes are down more than since the...  mostly-true
46569  the u s is spending one out of every six defen...         true
46570  says personhood legislation she sponsored woul...    half-true
46571  the republican party fought very hard in the s...         true
46572  a major part of the climate change bill sponso...        false
46573  ohios credit rating is as high as you can get aa         false
46574  says every day of a special session costs taxp...        false
46575   we ve excluded lobbyists from policymaking jobs         false
46576  the federal deficit would pay for gallons of n...    half-true
46577  says george flinn has been a no show at schedu...        false
46578  social security and other federal checks may n...    half-true
46579  tsa started off with screeners and the agency ...    half-true
46580  the proposed excise tax on cadillac health pla...  mostly-true
46581  i supported the surge i argued for it i m the ...        false
46582  says u s rep charles bass wants to privatize s...  barely-true
46583  more americans believe the moon landing was fa...    half-true
46584  in the past two years democrats have spent mor...   pants-fire
46585  for the first time in more than a decade impor...    ha

In [386]:
ori_df = pd.read_csv('data/combine_data.csv')
pre_df = pd.concat([token_df,ori_df['label']],axis=1)
pre_df

text        label
0      hous dem aid comey letter jason chaffetz tweet...            1
1      feel life circl roundabout head straight line ...            0
2      truth octob tension intellig analyst polit pol...            1
3      video civilian kill singl airstrik identifi ra...            1
4      print iranian woman sentenc year prison iran r...            1
5      tri time jacki mason voic reason week exclus c...            0
6      wonder britain icon pop pianist long flight pi...            1
7      pari franc chose idealist tradit candid sunday...            0
8      donald j trump schedul make highli anticip vis...            0
9      week michael flynn resign nation secur advis s...            0
10     organ action activist group morph barack obama...            0
11     bbc produc spoof real housew tv programm comed...            0
12     mysteri surround reich nazi germani subject de...            1
13     clinton campaign demand fbi affirm trump russi...            1
14     ye paid govern troll social media blog forum w...            1
15     guillermo barro schelotto argentin player set ...            0
16     scandal engulf fargo toppl chairman chief exec...            0
17     caddo nation tribal leader freed spend day bar...            1
18     fbi close hillari post home headlin world news...            1
19     wednesday donald trump press confer trump towe...            0
20     email donald trump enter elect year ago singl ...            1
21     screenwrit ryan murphi produc fx seri american...            0
22     sunday msnbc joy actor director rob reiner acc...            0
23     massachusett cop wife bust pin fake home invas...            1
24     order abort pill women seven latin american co...            0
25     email histor unit nation committe vote thursda...            1
26     jerusalem islam state sympath milit celebr nig...            0
27     humili hillari tri hide camera caught min rall...            1
28     andrea tantaro fox news host charg lawsuit fil...            0
29     hillari clinton sat hideaway studi ceremoni of...            0
...                                                  ...          ...
46560  say ron saunder choic stand rick scott expand ...        false
46561            presid obama took offic unemploy women     half-true
46562        peopl tax bracket wealthi small busi owner   barely-true
46563            barack obama pledg reduc size militari         false
46564  larg major public oppos major chang medicar fa...         true
46565                         fidel castro endors obama    pants-fire
46566  say spend fiscal budget lower spend fiscal bud...         true
46567  statist evid bail bond increas likelihood awai...        false
46568                              household incom year   mostly-true
46569            spend defens depart dollar afghanistan          true
46570  say personhood legisl sponsor restrict access ...    half-true
46571  republican parti fought hard civil right pass ...         true
46572  major climat chang sponsor sen john kerri joe ...        false
46573                          ohio credit rate high aa         false
46574               say day special session cost taxpay         false
46575                     exclud lobbyist policymak job         false
46576  feder deficit pay gallon new hampshir mapl syr...    half-true
46577                     say georg flinn schedul forum         false
46578    social secur feder check aug debt ceil increas     half-true
46579  tsa start screener agenc mushroom employe admi...    half-true
46580  propos excis tax cadillac health plan hit make...  mostly-true
46581                           support surg argu stage         false
46582       say rep charl bass want privat social secur   barely-true
46583  american believ moon land fake believ obamacar...    half-true
46584  past year democrat spent money countri spent y...   pants-fire
46585         time decad import account half oil consum     ha

In [398]:
pre_df.to_csv('data/pre_df.csv',index=False)
pre_df.label.unique() , len(pre_df)

(array(['1', '0', 'bias', 'conspiracy', 'fake', 'bs', 'satire', 'hate',
        'junksci', 'state', 'false', 'half-true', 'mostly-true', 'true',
        'barely-true', 'pants-fire'], dtype=object), 46590)

In [396]:
# df1_ = df1.drop(df1.loc[df1['label']=='bs'].index,axis=0)
# df1_ = df1_.drop(df1_.loc[df1_['label']=='half-true'].index,axis=0)
# df1_ = df1_.drop(df1_.loc[df1_['label']=='mostly-true'].index,axis=0)
# df1_ = df1_.drop(df1_.loc[df1_['label']=='barely-true'].index,axis=0)
# df1_.loc[df1_['label']=='0','label'] = 'true'
# df1_.loc[df1_['label']=='1','label'] = 'fake'
# df1_.loc[df1_['label']=='false','label'] = 'fake'
# df1_.loc[df1_['label']=='pants-fire','label'] = 'fake'
# df1_.reset_index(inplace=True,drop=True)

# df1_.to_csv('data/feature_selection_input.csv',index=False)
idx = (pre_df['label']=='bias')|(pre_df['label']=='bs')|(pre_df['label']=='conspiracy')|(pre_df['label']=='satire')|\
(pre_df['label']=='hate')|(pre_df['label']=='junksci')|(pre_df['label']=='state')
reg_df = pre_df.drop(pre_df.loc[idx].index,axis=0)
reg_df.loc[reg_df['label']=='1','label'] = 0 #fake
reg_df.loc[reg_df['label']=='0','label'] = 1 #true
reg_df.loc[reg_df['label']=='fake','label'] = 0
reg_df.loc[reg_df['label']=='false','label'] = 0
reg_df.loc[reg_df['label']=='half-true','label'] = 0.5
reg_df.loc[reg_df['label']=='mostly-true','label'] = 0.8
reg_df.loc[reg_df['label']=='true','label'] = 1
reg_df.loc[reg_df['label']=='barely-true','label'] = 0.2
reg_df.loc[reg_df['label']=='pants-fire','label'] = 0
print(reg_df.label.unique())
reg_df

[0 1 0.5 0.8 0.2]


text label
0      hous dem aid comey letter jason chaffetz tweet...     0
1      feel life circl roundabout head straight line ...     1
2      truth octob tension intellig analyst polit pol...     0
3      video civilian kill singl airstrik identifi ra...     0
4      print iranian woman sentenc year prison iran r...     0
5      tri time jacki mason voic reason week exclus c...     1
6      wonder britain icon pop pianist long flight pi...     0
7      pari franc chose idealist tradit candid sunday...     1
8      donald j trump schedul make highli anticip vis...     1
9      week michael flynn resign nation secur advis s...     1
10     organ action activist group morph barack obama...     1
11     bbc produc spoof real housew tv programm comed...     1
12     mysteri surround reich nazi germani subject de...     0
13     clinton campaign demand fbi affirm trump russi...     0
14     ye paid govern troll social media blog forum w...     0
15     guillermo barro schelotto argentin player set ...     1
16     scandal engulf fargo toppl chairman chief exec...     1
17     caddo nation tribal leader freed spend day bar...     0
18     fbi close hillari post home headlin world news...     0
19     wednesday donald trump press confer trump towe...     1
20     email donald trump enter elect year ago singl ...     0
21     screenwrit ryan murphi produc fx seri american...     1
22     sunday msnbc joy actor director rob reiner acc...     1
23     massachusett cop wife bust pin fake home invas...     0
24     order abort pill women seven latin american co...     1
25     email histor unit nation committe vote thursda...     0
26     jerusalem islam state sympath milit celebr nig...     1
27     humili hillari tri hide camera caught min rall...     0
28     andrea tantaro fox news host charg lawsuit fil...     1
29     hillari clinton sat hideaway studi ceremoni of...     1
...                                                  ...   ...
46560  say ron saunder choic stand rick scott expand ...     0
46561            presid obama took offic unemploy women    0.5
46562        peopl tax bracket wealthi small busi owner    0.2
46563            barack obama pledg reduc size militari      0
46564  larg major public oppos major chang medicar fa...     1
46565                         fidel castro endors obama      0
46566  say spend fiscal budget lower spend fiscal bud...     1
46567  statist evid bail bond increas likelihood awai...     0
46568                              household incom year    0.8
46569            spend defens depart dollar afghanistan      1
46570  say personhood legisl sponsor restrict access ...   0.5
46571  republican parti fought hard civil right pass ...     1
46572  major climat chang sponsor sen john kerri joe ...     0
46573                          ohio credit rate high aa      0
46574               say day special session cost taxpay      0
46575                     exclud lobbyist policymak job      0
46576  feder deficit pay gallon new hampshir mapl syr...   0.5
46577                     say georg flinn schedul forum      0
46578    social secur feder check aug debt ceil increas    0.5
46579  tsa start screener agenc mushroom employe admi...   0.5
46580  propos excis tax cadillac health plan hit make...   0.8
46581                           support surg argu stage      0
46582       say rep charl bass want privat social secur    0.2
46583  american believ moon land fake believ obamacar...   0.5
46584  past year democrat spent money countri spent y...     0
46585         time decad import account half oil consum    0.5
46586      say donald trump bankrupt compani twice time    0.8
46587  john mccain georg bush absolut plan univers he...     1
46588  new poll percent support presid plan reform he...     0
46589  claim report vindic new jersey gov chri christ...   0.2

[33610 rows x 2 columns]

In [397]:
reg_df.reset_index(inplace=True,drop=True)
reg_df.to_csv('data/reg_data_token.csv',index=False)
reg_df

text label
0      hous dem aid comey letter jason chaffetz tweet...     0
1      feel life circl roundabout head straight line ...     1
2      truth octob tension intellig analyst polit pol...     0
3      video civilian kill singl airstrik identifi ra...     0
4      print iranian woman sentenc year prison iran r...     0
5      tri time jacki mason voic reason week exclus c...     1
6      wonder britain icon pop pianist long flight pi...     0
7      pari franc chose idealist tradit candid sunday...     1
8      donald j trump schedul make highli anticip vis...     1
9      week michael flynn resign nation secur advis s...     1
10     organ action activist group morph barack obama...     1
11     bbc produc spoof real housew tv programm comed...     1
12     mysteri surround reich nazi germani subject de...     0
13     clinton campaign demand fbi affirm trump russi...     0
14     ye paid govern troll social media blog forum w...     0
15     guillermo barro schelotto argentin player set ...     1
16     scandal engulf fargo toppl chairman chief exec...     1
17     caddo nation tribal leader freed spend day bar...     0
18     fbi close hillari post home headlin world news...     0
19     wednesday donald trump press confer trump towe...     1
20     email donald trump enter elect year ago singl ...     0
21     screenwrit ryan murphi produc fx seri american...     1
22     sunday msnbc joy actor director rob reiner acc...     1
23     massachusett cop wife bust pin fake home invas...     0
24     order abort pill women seven latin american co...     1
25     email histor unit nation committe vote thursda...     0
26     jerusalem islam state sympath milit celebr nig...     1
27     humili hillari tri hide camera caught min rall...     0
28     andrea tantaro fox news host charg lawsuit fil...     1
29     hillari clinton sat hideaway studi ceremoni of...     1
...                                                  ...   ...
33580  say ron saunder choic stand rick scott expand ...     0
33581            presid obama took offic unemploy women    0.5
33582        peopl tax bracket wealthi small busi owner    0.2
33583            barack obama pledg reduc size militari      0
33584  larg major public oppos major chang medicar fa...     1
33585                         fidel castro endors obama      0
33586  say spend fiscal budget lower spend fiscal bud...     1
33587  statist evid bail bond increas likelihood awai...     0
33588                              household incom year    0.8
33589            spend defens depart dollar afghanistan      1
33590  say personhood legisl sponsor restrict access ...   0.5
33591  republican parti fought hard civil right pass ...     1
33592  major climat chang sponsor sen john kerri joe ...     0
33593                          ohio credit rate high aa      0
33594               say day special session cost taxpay      0
33595                     exclud lobbyist policymak job      0
33596  feder deficit pay gallon new hampshir mapl syr...   0.5
33597                     say georg flinn schedul forum      0
33598    social secur feder check aug debt ceil increas    0.5
33599  tsa start screener agenc mushroom employe admi...   0.5
33600  propos excis tax cadillac health plan hit make...   0.8
33601                           support surg argu stage      0
33602       say rep charl bass want privat social secur    0.2
33603  american believ moon land fake believ obamacar...   0.5
33604  past year democrat spent money countri spent y...     0
33605         time decad import account half oil consum    0.5
33606      say donald trump bankrupt compani twice time    0.8
33607  john mccain georg bush absolut plan univers he...     1
33608  new poll percent support presid plan reform he...     0
33609  claim report vindic new jersey gov chri christ...   0.2

[33610 rows x 2 columns]

clf

reg

test

In [363]:
dict_df3[df1.index,'vote'] +=1

TypeError: unhashable type: 'Int64Index'

In [258]:
# len(class_token_dict[cat[c]])
class_token_dict_={}
for k,v in class_token_dict.items():
    rev_cat=[]
    for r in v:
        rev = list(set(r.split(' ')))
        rev_cat.extend(rev)
    class_token_dict_[k]=rev_cat
class_token_dict_[cat[c]]

['',
 'brilliant',
 'sort',
 'time',
 'demonstr',
 'test',
 'speak',
 'ill',
 'follow',
 'littl',
 'complic',
 'fact',
 'figur',
 'diagnost',
 'awar',
 'scratch',
 'goe',
 'taken',
 'contraposit',
 'subconsci',
 'exampl',
 'right',
 'blurt',
 'neuroscientist',
 'know',
 'tool',
 'deduc',
 'post',
 'angl',
 'think',
 'way',
 'left',
 'articl',
 'ton',
 'schizophren',
 'unconsci',
 'head',
 'thing',
 'race',
 'continu',
 'process',
 'premis',
 'activ',
 'exist',
 'question',
 'normal',
 'schizophrenia',
 'object',
 'worri',
 'cue',
 'car',
 'pass',
 'simpl',
 'box',
 'make',
 'world',
 'extent',
 'respons',
 'outsid',
 'need',
 'psychiatrist',
 'power',
 'reason',
 'far',
 'geniu',
 'hurrican',
 'research',
 'proper',
 'super',
 'second',
 'answer',
 'estim',
 'brain',
 'guess',
 'unrel',
 'hint',
 'word',
 'purpos',
 'non',
 'true',
 'evalu',
 'item',
 'heavili',
 'method',
 'sourc',
 'patient',
 'genius',
 'reli',
 'concern',
 'help',
 'influenc',
 'peopl',
 'assum',
 'quiz',
 'person'

In [259]:
len(class_token_dict_['fake'])

1989419

In [248]:
cat = df1_.label.unique().tolist()
for term in tqdm(terms): #each term
    scores = []
    scores_chi = []
    scores_emi = []
    c=0
    for _ in range(len(class_token_dict)): # each class
        n11=e11=m11=0
        n10=e10=m10=0
        n01=e01=m01=0
        n00=e00=m00=0
        for k,v in class_token_dict.items():
#             print(k,c)
            if k == cat[c]: #ontopic
                for r in v: #所有這一類的文章
                    if term in (set(r.split(' '))): #term在某一篇文章裡面
                        n11+=1
                    else:
                        n10+=1
#                 c+=1
            else: #off topic
                for r in v:
                    if term in (set(r.split(' '))):
                        n01+=1
                    else:
                        n00+=1
#                 c+=1
        c+=1
        n11+=1e-8
        n10+=1e-8
        n01+=1e-8
        n00+=1e-8
        N = n11+n10+n01+n00
        e11 = N * (n11+n01)/N * (n11+n10)/N #chi-squre
        e10 = N * (n11+n10)/N * (n10+n00)/N
        e01 = N * (n11+n01)/N * (n01+n00)/N
        e00 = N * (n01+n00)/N * (n10+n00)/N
        score_chi = ((n11-e11)**2)/e11 + ((n10-e10)**2)/e10 + ((n01-e01)**2)/e01 + ((n00-e00)**2)/e00
        scores_chi.append(score_chi)
        
        n11 = n11 - 1e-8 + 1e-6
        n10 = n10 - 1e-8 + 1e-6
        n01 = n01 - 1e-8 + 1e-6
        n00 = n00 - 1e-8 + 1e-6
        N = n11+n10+n01+n00
        m11 = (n11/N) * math.log(((n11/N)/((n11+n01)/N * (n11+n10)/N)),2) #EMI
        m10 = n10/N * math.log((n10/N)/((n11+n10)/N * (n10+n00)/N),2)
        m01 = n01/N * math.log((n01/N)/((n11+n01)/N * (n01+n00)/N),2)
        m00 = n00/N * math.log((n00/N)/((n01+n00)/N * (n10+n00)/N),2)
        score_emi = m11 + m10 + m01 + m00
        scores_emi.append(score_emi)
        
#         print(n11,n10,n01,n00)
        n11= n11- 1e-6 + 1e-20
        n10= n10 - 1e-6 + 1e-20
        n01= n01 - 1e-6 + 1e-20
        n00= n00 - 1e-6 + 1e-20
        N = n11+n10+n01+n00
        try:
            score = (((n11+n01)/N) ** n11) * ((1 - ((n11+n01)/N)) ** n10) * (((n11+n01)/N) ** n01) * ((1 - ((n11+n01)/N)) ** n00)
            score /= ((n11/(n11+n10)) ** n11) * ((1 - (n11/(n11+n10))) ** n10) * ((n01/(n01+n00)) ** n01) * ((1 - (n01/(n01+n00))) ** n00)
            score = -2 * math.log(score, 10) #LLR
        except :
            score = 0
        scores.append(score)
        
        
#         c+=1
    dict_df.loc[term,'score_llr'] = np.mean(scores)
    dict_df.loc[term,'score_chi'] = np.mean(scores_chi)
    dict_df.loc[term,'score_emi'] = np.mean(scores_emi)
dict_df    






  0%|          | 0/50097 [00:00<?, ?it/s]




  0%|          | 1/50097 [00:05<73:00:50,  5.25s/it]




  0%|          | 2/50097 [00:10<72:50:15,  5.23s/it]




  0%|          | 3/50097 [00:15<72:48:18,  5.23s/it]




  0%|          | 4/50097 [00:20<72:45:20,  5.23s/it]




  0%|          | 5/50097 [00:26<72:45:12,  5.23s/it]




  0%|          | 6/50097 [00:31<72:44:22,  5.23s/it]




  0%|          | 7/50097 [00:36<72:43:44,  5.23s/it]




  0%|          | 8/50097 [00:41<72:42:54,  5.23s/it]




  0%|          | 9/50097 [00:47<72:42:06,  5.23s/it]




  0%|          | 10/50097 [00:52<72:41:25,  5.22s/it]




  0%|          | 11/50097 [00:57<72:40:40,  5.22s/it]




  0%|          | 12/50097 [01:02<72:43:12,  5.23s/it]




  0%|          | 13/50097 [01:07<72:44:27,  5.23s/it]




  0%|          | 14/50097 [01:13<72:44:08,  5.23s/it]




  0%|          | 15/50097 [01:18<72:43:40,  5.23s/it]




  0%|          | 16/50097 [01:23<72:43:07,  5.23s/it]




  0%|          | 17/50097 [01:

  0%|          | 222/50097 [19:22<72:32:45,  5.24s/it]




  0%|          | 223/50097 [19:27<72:32:40,  5.24s/it]




  0%|          | 224/50097 [19:33<72:32:52,  5.24s/it]




  0%|          | 225/50097 [19:38<72:32:44,  5.24s/it]




  0%|          | 226/50097 [19:43<72:32:39,  5.24s/it]




  0%|          | 227/50097 [19:48<72:32:43,  5.24s/it]




  0%|          | 228/50097 [19:54<72:32:36,  5.24s/it]




  0%|          | 229/50097 [19:59<72:32:29,  5.24s/it]




  0%|          | 230/50097 [20:04<72:32:21,  5.24s/it]




  0%|          | 231/50097 [20:09<72:32:13,  5.24s/it]




  0%|          | 232/50097 [20:14<72:32:05,  5.24s/it]




  0%|          | 233/50097 [20:20<72:32:00,  5.24s/it]

KeyboardInterrupt: 

In [247]:
'gop' in (set(r.split(' ')))

True

In [216]:
((n11/(n11+n10)) ** n11) * ((1 - (n11/(n11+n10))) ** n10) * ((n01/(n01+n00)) ** n01) * ((1 - (n01/(n01+n00))) ** n00)


0.0

In [187]:
ori_df.to_dict()

{'text': {0: 'house dem aide we didn t even see comey s letter until jason chaffetz tweeted it by darrell lucus on october subscribe jason chaffetz on the stump in american fork utah image courtesy michael jolley available under a creative commons by license with apologies to keith olbermann there is no doubt who the worst person in the world is this week fbi director james comey but according to a house democratic aide it looks like we also know who the second worst person is as well it turns out that when comey sent his now infamous letter announcing that the fbi was looking into emails that may be related to hillary clinton s email server the ranking democrats on the relevant committees didn t hear about it from comey they found out via a tweet from one of the republican committee chairmen as we now know comey notified the republican chairmen and democratic ranking members of the house intelligence judiciary and oversight committees that his agency was reviewing emails it had recent

In [159]:
sum([1,2,3])

6

In [57]:
df['df'].quantile(0.99) , df['df'].max() , df['df'].quantile(0.25),df['df'].quantile(0.75)

(1376.0, 18681, 1.0, 7.0)

In [66]:
news

'claim report vindic new jersey gov chri christi bridg scandal conclus '

In [84]:
news_li = news.split(' ')

kk = list(newdict)

kkk = newdict.values()
np.array(list(kkk))

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])

In [87]:
kk
newdict

{'claim': 1,
 'report': 1,
 'vindic': 1,
 'new': 1,
 'jersey': 1,
 'gov': 1,
 'chri': 1,
 'christi': 1,
 'bridg': 1,
 'scandal': 1,
 'conclus': 1}

In [107]:
kk = df.loc[df['term'].isin(keys),'tf']
kk = kk.reset_index().index.tolist()
np.array(values)[kk]

array([ 6,  2,  5, 10,  7,  5, 14,  5,  5,  2,  2,  1,  1,  1,  1,  2,  1,
        2,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  4,  3,  3,  1,  6,  2,
        1,  3,  8,  3,  3,  8,  2,  5,  1,  1,  1,  5,  1,  2,  1,  1,  5,
        2,  7,  1,  8,  4,  2,  5,  1,  1,  3,  1,  2,  1,  1,  1,  1,  1,
        2,  1,  1,  2,  1,  2,  1,  1,  1,  1,  1,  1,  3,  4,  1,  1,  1,
        1,  1,  2,  1,  1,  1,  1,  1,  2,  1,  1,  2,  1,  1,  1,  1,  1,
        2,  2,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,
        1,  1,  1,  1,  2,  1,  3,  2,  1,  1,  1,  2,  1,  3,  1,  1,  1,
        1,  1,  2,  1,  1,  1,  1,  2,  2,  1,  1,  1,  1,  1,  2,  1,  1,
        2,  3,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,
        1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  2,  1,  1,
        1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,  1,
        1,  1,  1,  1,  1,  1,  1,  1,  2,  1,  1,  1,  1,  2,  1,  1,  1,
        1,  1,  1,  1,  1

In [100]:
np.array(df.loc[df['term'].isin(keys),'tf'].index.tolist())

array([   358,    572,    695,    950,   1002,   1408,   1741,   2040,
         3614,   3999,   4457,   4571,   4620,   5109,   5161,   5180,
         6891,   7480,   9145,  11563,  13036,  13850,  14875,  15024,
        16250,  16403,  17301,  17331,  17334,  17561,  17748,  18483,
        19219,  19368,  19431,  20021,  20033,  20258,  20353,  20363,
        20987,  21103,  21271,  21454,  21551,  21566,  22139,  22203,
        22213,  22521,  23263,  23847,  24023,  24241,  24242,  24600,
        24767,  25329,  25437,  26052,  26365,  27131,  27151,  27302,
        27608,  28455,  29115,  30837,  31050,  31869,  33534,  33688,
        33764,  33830,  34124,  34161,  34278,  34562,  34895,  35935,
        36546,  36809,  38894,  40455,  41181,  41251,  41353,  41426,
        41543,  41656,  42170,  44419,  44501,  45581,  46699,  46768,
        48294,  48820,  48865,  48949,  49140,  49225,  49402,  49696,
        49792,  50218,  50803,  51402,  51595,  51598,  52578,  52744,
      

In [6]:
ori_df.label.unique()

array(['1', '0', 'bias', 'conspiracy', 'fake', 'bs', 'satire', 'hate',
       'junksci', 'state', 'false', 'half-true', 'mostly-true', 'true',
       'barely-true', 'pants-fire'], dtype=object)